In [1]:
import numpy as np
import pandas as pd
from datetime import datetime,date

In [2]:
from pandas_profiling import ProfileReport


In [3]:
pip show pandas_profiling

Name: pandas-profiling
Version: 2.7.1
Summary: Generate profile report for pandas DataFrame
Home-page: https://github.com/pandas-profiling/pandas-profiling
Author: Simon Brugman
Author-email: pandasprofiling@gmail.com
License: MIT
Location: /Users/abianco/opt/anaconda3/lib/python3.9/site-packages
Requires: astropy, confuse, htmlmin, ipywidgets, jinja2, joblib, matplotlib, missingno, numpy, pandas, phik, requests, scipy, tangled-up-in-unicode, tqdm, visions
Required-by: 
Note: you may need to restart the kernel to use updated packages.


In [4]:
df_311 = pd.read_csv('311_Service_Requests_from_2010_to_Present.csv')

In [5]:
print(df_311.shape)
df_311.head(1)

(1013986, 41)


Unique Key            Created Date             Closed Date Agency  \
0    37666285  11/12/2017 12:00:00 AM  01/22/2018 12:00:00 AM    HPD   

                                         Agency Name  Complaint Type  \
0  Department of Housing Preservation and Develop...  HEAT/HOT WATER   

       Descriptor         Location Type  Incident Zip    Incident Address  \
0  APARTMENT ONLY  RESIDENTIAL BUILDING       10034.0  165 SHERMAN AVENUE   

   ... Vehicle Type  Taxi Company Borough  Taxi Pick Up Location  \
0  ...          NaN                   NaN                    NaN   

   Bridge Highway Name  Bridge Highway Direction Road Ramp  \
0                  NaN                       NaN       NaN   

  Bridge Highway Segment   Latitude  Longitude  \
0                    NaN  40.864764 -73.922764   

                                  Location  
0  (40.86476431663921, -73.92276447154296)  

[1 rows x 41 columns]

In [6]:
profile_all = ProfileReport(df_311, html={'style':{'full_width':True}})

profile_all.to_notebook_iframe()

profile_all.to_file(output_file='311output.html')

Summarize dataset:   0%|          | 0/53 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
# drop columns that are not in our Complaint data mart dimension model

keep_lst = ['Unique Key','Complaint Type','Descriptor','Status'
            ,'Agency Name','Open Data Channel Type','Created Date'
            ,'Borough','Location Type','Incident Address','City'
            ,'Incident Zip','Latitude','Longitude','Resolution Description']

df_hh = df_311.drop(columns=[col for col in df_311 if col not in keep_lst])

In [8]:
# remove whitespace from column names
df_hh.columns = df_hh.columns.str.replace(' ', '_')

print(df_hh.columns)

Index(['Unique_Key', 'Created_Date', 'Agency_Name', 'Complaint_Type',
       'Descriptor', 'Location_Type', 'Incident_Zip', 'Incident_Address',
       'City', 'Status', 'Resolution_Description', 'Borough',
       'Open_Data_Channel_Type', 'Latitude', 'Longitude'],
      dtype='object')


In [9]:
# fill nans with 'Unspecified'
df_hh.dropna(inplace=True)

df_hh = df_hh[df_hh['Borough'] != 'Unspecified']

print(df_hh['Borough'].unique())
print(df_hh['Open_Data_Channel_Type'].unique())

['MANHATTAN' 'BRONX' 'BROOKLYN' 'QUEENS' 'STATEN ISLAND']
['PHONE' 'ONLINE' 'MOBILE']


In [10]:
print(df_hh.shape)

(1006878, 15)


In [12]:
# replace Created_Date (object) with Created_Date (date)

#df_hh['Created_Date'] = pd.to_datetime(df_hh['Created_Date']).dt.date
df_hh['Created_Date'] = df_hh['Created_Date'].astype('datetime64[ns]')

print(df_hh['Created_Date'].dtype, df_hh['Created_Date'][1])

datetime64[ns] 2017-11-12 00:00:00


In [13]:
# change case of fields to be uniformed and more readable

str_title_lst = ['Borough','Complaint_Type','Descriptor','Location_Type'
                  ,'Incident_Address', 'City','Open_Data_Channel_Type']

def series_title_case(lst):
  for i in lst:
    df_hh[i] = df_hh[i].str.title()
    df_hh[i] = df_hh[i].str.strip()

    print(df_hh[i][1])

series_title_case(str_title_lst)

Bronx
Heat/Hot Water
Apartment Only
Residential Building
353 East  141 Street
Bronx
Online


In [14]:
# update dtypes for Latitude and Longitude
df_hh['Latitude'] = df_hh['Latitude'].astype('float')
df_hh['Longitude'] = df_hh['Longitude'].astype('float')
df_hh['Incident_Zip'] = df_hh['Incident_Zip'].astype('int')

In [15]:
df_hh.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1006878 entries, 0 to 1013985
Data columns (total 15 columns):
 #   Column                  Non-Null Count    Dtype         
---  ------                  --------------    -----         
 0   Unique_Key              1006878 non-null  int64         
 1   Created_Date            1006878 non-null  datetime64[ns]
 2   Agency_Name             1006878 non-null  object        
 3   Complaint_Type          1006878 non-null  object        
 4   Descriptor              1006878 non-null  object        
 5   Location_Type           1006878 non-null  object        
 6   Incident_Zip            1006878 non-null  int64         
 7   Incident_Address        1006878 non-null  object        
 8   City                    1006878 non-null  object        
 9   Status                  1006878 non-null  object        
 10  Resolution_Description  1006878 non-null  object        
 11  Borough                 1006878 non-null  object        
 12  Open_Data_Chan

In [16]:
print(df_hh.shape)
df_hh.head()

(1006878, 15)


Unique_Key Created_Date                                        Agency_Name  \
0    37666285   2017-11-12  Department of Housing Preservation and Develop...   
1    37675276   2017-11-12  Department of Housing Preservation and Develop...   
2    37682385   2017-11-13  Department of Housing Preservation and Develop...   
3    38112583   2018-01-04  Department of Housing Preservation and Develop...   
4    38792282   2018-03-27  Department of Housing Preservation and Develop...   

   Complaint_Type       Descriptor         Location_Type  Incident_Zip  \
0  Heat/Hot Water   Apartment Only  Residential Building         10034   
1  Heat/Hot Water   Apartment Only  Residential Building         10454   
2  Heat/Hot Water  Entire Building  Residential Building         11238   
3  Heat/Hot Water  Entire Building  Residential Building         10031   
4  Heat/Hot Water  Entire Building  Residential Building         11216   

       Incident_Address      City  Status  \
0    165 Sherman Avenue  New York  Closed   
1  353 East  141 Street     Bronx  Closed   
2    374 Prospect Place  Brooklyn  Closed   
3  38 St Nicholas Place  New York  Closed   
4     159 Halsey Street  Brooklyn  Closed   

                              Resolution_Description    Borough  \
0  The Department of Housing Preservation and Dev...  Manhattan   
1  The Department of Housing Preservation and Dev...      Bronx   
2  The Department of Housing Preservation and Dev...   Brooklyn   
3  The Department of Housing Preservation and Dev...  Manhattan   
4  The Department of Housing Preservation and Dev...   Brooklyn   

  Open_Data_Channel_Type   Latitude  Longitude  
0                  Phone  40.864764 -73.922764  
1                 Online  40.811517 -73.922606  
2                 Online  40.676712 -73.964359  
3                  Phone  40.828537 -73.941463  
4                  Phone  40.682097 -73.947385

In [17]:
for columns in df_hh:
  print(columns, df_hh[columns].unique()[:6])

Unique_Key [37666285 37675276 37682385 38112583 38792282 38793312]
Created_Date ['2017-11-12T00:00:00.000000000' '2017-11-13T00:00:00.000000000'
 '2018-01-04T00:00:00.000000000' '2018-03-27T00:00:00.000000000'
 '2017-08-04T00:00:00.000000000' '2017-08-15T00:00:00.000000000']
Agency_Name ['Department of Housing Preservation and Development'
 'Division of Alternative Management']
Complaint_Type ['Heat/Hot Water']
Descriptor ['Apartment Only' 'Entire Building']
Location_Type ['Residential Building']
Incident_Zip [10034 10454 11238 10031 11216 11203]
Incident_Address ['165 Sherman Avenue' '353 East  141 Street' '374 Prospect Place'
 '38 St Nicholas Place' '159 Halsey Street' '374 East   49 Street']
City ['New York' 'Bronx' 'Brooklyn' 'Elmhurst' 'Corona' 'Forest Hills']
Status ['Closed' 'Open']
Resolution_Description ['The Department of Housing Preservation and Development has closed this complaint administratively. Please file a new complaint through 311MOBILE, 311ONLINE or by calling 311 

In [18]:
df_hh.to_csv('cleaned_311complaints_Final.csv')

In [19]:
profile_hh_final = ProfileReport(df_hh)

profile_hh_final.to_notebook_iframe()

profile_hh_final.to_file(output_file='hh_final_output.html')

Summarize dataset:   0%|          | 0/28 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]